# Trips - Analysis
Broad to-do:
- ~~consolidate csv to one trip per row~~ done in tsrtc8
- drop trips with blank or odd timings
- generate gtfs calendar.txt, trips.txt and stop_times.txt

In [1]:
import pandas as pd
from collections import OrderedDict
import numpy as np
import openpyxl
import os.path
from ast import literal_eval # for parsing list stored as string back into list
from save2Excel import save2Excel

/mnt/7ACA0CC0CA0C7B21/temp/py36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
# loading the tripwise-gouped file processed at the end of tsrtc10.
df = pd.read_csv('grouped-tripwise.csv', dtype=str, index_col='sr').fillna('')
# typecasting all columns as text, so that concat etc operations are simpler to do further along.
print(df.shape)
df.columns

(35550, 36)


Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id',
       'gtfs_direction_id', 'trip_short_name'],
      dtype='object')

In [3]:
'#'*100

'####################################################################################################'

# Analysis

## finding timespan of each trip
ie, last stop's timestamp - first stop's timestamp

In [4]:
# converting some columns back to int, list etc

if isinstance(df.num_stops.iloc[0], str):
    print('Before:num_stops:',type(df.num_stops.iloc[0]) )
    df['num_stops'] = df.num_stops.apply(lambda x: literal_eval(x))
    print('After:num_stops:',type(df.num_stops.iloc[0]) )
else: print('num_stops: you\'re fine')

if isinstance(df.FROM_TIME.iloc[0], str):
    print('Before:FROM_TIME:',type(df.FROM_TIME.iloc[0]) )
    df['FROM_TIME'] = df.FROM_TIME.apply(lambda x: literal_eval(x))
    print('After:FROM_TIME:',type(df.FROM_TIME.iloc[0]) )
else: print('FROM_TIME: you\'re fine')

if isinstance(df.FROM_TIME_num.iloc[0], str):
    print('Before:FROM_TIME_num:',type(df.FROM_TIME_num.iloc[0]) )
    df['FROM_TIME_num'] = df.FROM_TIME_num.apply(lambda x: literal_eval(x))
    print('After:FROM_TIME_num:',type(df.FROM_TIME_num.iloc[0]) )
else: print('FROM_TIME_num: you\'re fine')


Before:num_stops: <class 'str'>
After:num_stops: <class 'numpy.int64'>
Before:FROM_TIME: <class 'str'>
After:FROM_TIME: <class 'list'>
Before:FROM_TIME_num: <class 'str'>
After:FROM_TIME_num: <class 'list'>


In [5]:
# sample cell: [1235, 1239, 1243, 1248, 1252, 1257, 1261, 1266, 1270, 1275]
df['timespan'] = df.FROM_TIME_num.apply( lambda x: x[-1] - x[0])
print(df.timespan.head(10))
print('max:',df.timespan.max(),', min:',df.timespan.min(),', median:',df.timespan.median(),', avg:',df.timespan.mean())

sr
0    40
1    15
2    90
3    90
4    90
5    90
6    90
7    90
8    15
9    15
Name: timespan, dtype: int64
max: 1210 , min: 0 , median: 55.0 , avg: 55.82475386779184


### > timespans of the trips range from 0 mins to 1210 mins

## trips with zero timespan (ie where timestamps are all the same)
and no, the case of plus-minus isn't there as those kinds of trips that aren't having timings in ascending order were flagged and removed.

In [6]:
df[ df.timespan == 0].shape

(19, 37)

In [7]:
df[ df.timespan == 0].TRIP_ID.unique() # could use tolist() too but this makes them appear horizontally.

array(['60232', '60743', '63046', '75684', '81157', '82097', '85665',
       '86068', '86096', '86101', '86160', '86161', '86200', '86201',
       '86241', '86254', '91643', '91687', '97147'], dtype=object)

#### > these are flagged in warnings by feed validator, but there are other trips too flagged there whose some if not all stops are having same timestamps.

In [8]:
df[ df.timespan == 0].groupby('ROUTE_NUMBER').TRIP_ID.count()

ROUTE_NUMBER
10K       1
127K      1
16A       1
19M       1
203A/R    1
280       1
288D      1
5K/92     1
8J/M      8
8R        3
Name: TRIP_ID, dtype: int64

### > 19 trips under 10 routes, with 8J/M having 8 trips : these have identical timestamps for all stops.
not removing them from main trips data, as the gtfs validator doesn't strike them as error but warning.

In [9]:
df.columns

Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id',
       'gtfs_direction_id', 'trip_short_name', 'timespan'],
      dtype='object')

In [10]:
if isinstance(df.crossMidnight.iloc[0], str):
    print('Before:crossMidnight:',type(df.crossMidnight.iloc[0]) )
    df['crossMidnight'] = df.crossMidnight.apply(lambda x: literal_eval(x))
    print('After:crossMidnight:',type(df.crossMidnight.iloc[0]) )
else: print('crossMidnight: you\'re fine')

Before:crossMidnight: <class 'str'>
After:crossMidnight: <class 'numpy.bool_'>


In [11]:
df[ df['crossMidnight']][['ROUTE_NUMBER','TRIP_ID','FROM_TIME','FROM_TIME_NEW']]

ROUTE_NUMBER TRIP_ID       FROM_TIME       FROM_TIME_NEW
sr                                                              
219    MGBS-TIRUPATI  115356  [16:00, 02:35]  ['16:00', '26:35']
1199    B.PALLY-ATNR  136221  [19:35, 03:15]  ['19:35', '27:15']
9856   MGBS-TIRUPATI   56630  [20:20, 07:00]  ['20:20', '31:00']
14633            VJA   64509  [22:15, 00:10]  ['22:15', '24:10']
14667            VJA   64548  [23:15, 01:10]  ['23:15', '25:10']
15876             9F   65955  [23:45, 00:00]  ['23:45', '24:00']

## grouping by length of trip
ie, number of stops

In [12]:
df.num_stops.sort_values().unique()

array([ 2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18,
       19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 33, 34, 36, 37,
       38, 42, 52, 53])

In [13]:
def tripLengths_grouping(x):
    names = OrderedDict({
        'num_trips': len(set(x['TRIP_ID'])),
        'num_routes': len(set(x['ROUTE_NUMBER'])),
        'num_depots': len(set(x['DEPOT_CODE'])),
        'num_services': len(set(x['SERVICE_ID'])),
        'num_service_types': len(set(x['SERVICE_TYPE'])),
        'timespan': x.timespan.sort_values().unique(),
        'max_timespan': x.timespan.max(),
        'min_timespan': x.timespan.min(),
    })
    return pd.Series(names)

In [14]:
tripLengths = df.groupby('num_stops').apply(tripLengths_grouping)
tripLengths

num_trips  num_routes  num_depots  num_services  num_service_types  \
num_stops                                                                       
2                793          19           5           105                  5   
3                600          23          11            97                 12   
4               2188          63          22           273                 16   
5               2579          85          22           356                 18   
6               2481          73          21           315                 15   
7               1284          45          15           134                 12   
8               2522          62          22           297                 19   
9               2099          45          20           282                 15   
10              3259          55          21           377                 13   
11              1991          46          22           255                 15   
12              1669          40          17           210                 13   
13              2009          33          16           274                 13   
14              1170          32          14           153                 12   
15              1116          26          16           133                  7   
16              1088          19          11           150                  8   
17              1019          21          10           138                 10   
18              1088          18          12           153                 11   
19               788          11           9           130                 10   
20               893          13           8           143                  9   
21              1264          12           8           204                  8   
22               615          14           9           112                 12   
23               584          16          11            97                 14   
24               360          10           6            44                  9   
25               436           8           6            63                  7   
26               418           6           3            56                  6   
27               428           6           5            72                  7   
28               121           4           2            17                  4   
29                98           3           3            23                  4   
30                37           3           3             4                  3   
31                35           1           1             6                  1   
33                84           1           1            13                  1   
34                30           1           2             5                  3   
36                 9           1           1             3                  1   
37                96           1           1            14                  2   
38                 8           1           1             1                  1   
42                25           1           1             3                  1   
52                33           1           1             6                  1   
53               233           1           1            34                  1   

                                                    timespan  max_timespan  \
num_stops                                                                    
2          [3, 5, 10, 15, 20, 30, 35, 36, 40, 42, 44, 45,...           640   
3          [2, 5, 10, 20, 25, 35, 43, 48, 50, 55, 60, 65,...           415   
4          [0, 1, 2, 4, 5, 8, 9, 10, 15, 20, 22, 23, 25, ...           650   
5          [2, 3, 5, 8, 10, 15, 18, 19, 20, 22, 25, 30, 3...           330   
6          [1, 2, 3, 4, 5, 9, 10, 14, 15, 16, 19, 20, 24,...          1210   
7          [0, 2, 5, 10, 15, 20, 25, 27, 28, 30, 32, 33, ...           680   
8          [2, 5, 10, 13, 14, 15, 20, 24, 25, 26, 27, 30,...           300   
9          [0, 2, 5, 10, 15, 17, 20, 23, 25, 28, 29, 30, ...        

In [15]:
tripLengths.shape

(38, 8)

In [16]:
tripLengths.to_csv('tripLengths_grouping.csv')

In [17]:
save2Excel(tripLengths,'TripLengths_grouping')

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot', 'Trips_OddTimings']
Sheet TripLengths_grouping added to TSRTC-analysis.xlsx


In [18]:
'#'*100

'####################################################################################################'

In [19]:
df.columns

Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id',
       'gtfs_direction_id', 'trip_short_name', 'timespan'],
      dtype='object')

## grouping by service types


In [20]:
if isinstance(df.STAGE_ID.iloc[0], str):
    print('Before:STAGE_ID:',type(df.STAGE_ID.iloc[0]) )
    df['STAGE_ID'] = df.STAGE_ID.apply(lambda x: literal_eval(x))
    print('After:STAGE_ID:',type(df.STAGE_ID.iloc[0]) )
else: print('STAGE_ID: you\'re fine')

Before:STAGE_ID: <class 'str'>
After:STAGE_ID: <class 'list'>


In [21]:
df.STAGE_ID.tolist()

[['14611',
  '14610',
  '8326',
  '13260',
  '8059',
  '8345',
  '6936',
  '1997',
  '1133',
  '182'],
 ['6764', '8550', '688', '8501', '3484'],
 ['6764', '688', '8550', '3484', '8501'],
 ['3484', '8501', '688', '8550', '6764'],
 ['8550', '688', '6764', '8501', '3484'],
 ['3484', '8501', '688', '6764', '8550'],
 ['6764', '8550', '688', '8501', '3484'],
 ['8501', '3484', '6764', '8550', '688'],
 ['3484', '8501', '6764', '8550', '688'],
 ['8550', '6764', '688', '8501', '3484'],
 ['8550', '6764', '688', '8501', '3484'],
 ['3484', '8501', '6764', '8550', '688'],
 ['8550', '6764', '688', '8501', '3484'],
 ['3484', '8501', '6764', '688', '8550'],
 ['6764', '688', '8550', '3484', '8501'],
 ['8501', '3484', '8550', '6764', '688'],
 ['8501', '3484', '6764', '8550', '688'],
 ['6764', '8550', '688', '8501', '3484'],
 ['688', '8550', '6764', '3484', '8501'],
 ['3484', '8501', '688', '8550', '6764'],
 ['6764', '8550', '688', '3484', '8501'],
 ['8501', '3484', '6764', '8550', '688'],
 ['688', '6764'

In [22]:
def service_type_grouping(x):
    names = OrderedDict({
        'count': len(x),
        'num_trips': len(set(x['TRIP_ID'])),
        'num_depots': len(set(x['DEPOT_CODE'])),
        'num_service_ids': len(set(x['SERVICE_ID'])),
        'num_routes': len(set(x['ROUTE_NUMBER'])),
        'num_calendar_ids': len(set(x['gtfs_calendar_id'])),
        'num_stops': len(set([item for sublist in x.STAGE_ID for item in sublist]))
    })
    return pd.Series(names)

In [23]:
serviceTypeGroup = df.groupby('SERVICE_TYPE').apply(service_type_grouping)
serviceTypeGroup

count  num_trips  num_depots  num_service_ids  num_routes  \
SERVICE_TYPE                                                              
AC               60         60           1               10           1   
AE              417        417           2               41           6   
CO            13442      13442          24             1683         245   
CS              316        316           4               62           3   
CV              146        146           3               46           4   
FS             1521       1521          13              242          32   
IB              121        121           3               17           2   
IH              155        155          10               32          18   
IM               20         20           2                4           3   
LA              163        163           5               36           6   
LB              675        675           4              128           7   
LN              126        126           1               22           3   
MA             1055       1055           3               96          32   
ME              777        777          18              134          38   
MF              208        208           1               25           9   
MO              868        868          13              113          54   
MS               88         88           4               12           3   
PA              560        560          11               72          15   
PC              407        407           5               36           7   
PM              386        386          10               47          31   
PN              152        152           5               16           6   
PO               10         10           1                1           1   
PS             1790       1790          17              208          81   
SA              210        210           2               27          10   
SN             5534       5534          25              844         115   
SU             5143       5143          22              602         115   
VB               60         60           2                8           2   
VC               87         87           4               15           6   
VR              363        363           6               82          18   
XC              552        552           2               68          15   
XF                8          8           1                2           1   
XG               87         87           1               16           3   
XM               30         30           1                4           2   
XS               13         13           1                1           1   

              num_calendar_ids  num_stops  
SERVICE_TYPE                               
AC                           1         19  
AE                           3         31  
CO                          18        803  
CS                           5         44  
CV                           5         68  
FS                           5        271  
IB                           3         21  
IH                           5         68  
IM                           1         22  
LA                           6         89  
LB                           5         76  
LN                           1         17  
MA                           4        112  
ME                           6        267  
MF                           4         41  
MO                           3        326  
MS                           4         79  
PA                           3        183  
PC                           1         73  
PM                           1        241  
PN                           3         57  
PO                           1          5  
PS                           6        435  
SA                           3         26  
SN                           8        458  
SU                          13        586  
VB                           4         12  
VC                           3       

In [24]:
save2Excel(serviceTypeGroup,'serviceType_grouping')

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot', 'Trips_OddTimings', 'TripLengths_grouping']
Sheet serviceType_grouping added to TSRTC-analysis.xlsx


In [25]:
'#'*100

'####################################################################################################'

## depot codes export

In [29]:
df.DEPOT_CODE.unique()

array(['KCG', 'MI2', 'JDM', 'HN1', 'HN2', 'KGD', 'CNT', 'FMA', 'UPL',
       'BKP', 'RN2', 'DSR', 'MPM', 'MS2', 'RJN', 'FNR', 'MS1', 'MHM',
       'BGD', 'MDN', 'BHL', 'KPL', 'HPT', 'MI1', 'CCL', 'HCU', 'RN1'],
      dtype=object)

In [30]:
df.DEPOT_CODE.drop_duplicates().sort_values().to_csv('depot_code.csv',index=False)

## finding details about the blank route_number

In [31]:
df[ df.ROUTE_NUMBER == 'BLANK'].CURRENT_STAGE_NAME.iloc[0]

"['CHENGICHERLA-DEPOT', 'CHENGICHERLA', 'RTC-COLONY-CHENEGICHERLA', 'MEDIPALLY', 'PEERAZADI-GUDA', 'UPPAL-BUS-STAND', 'MODERN-BAKERY', 'RAMANTHAPUR-PUBLIC-SCHOOL', 'AMBERPET-GANDHI-STATUE', 'KACHIGUDA', 'KOTI']"

In [32]:
len( df[ df.ROUTE_NUMBER == 'BLANK'] )

37

In [33]:
df[ df.ROUTE_NUMBER == 'BLANK'].groupby('gtfs_direction_id').gtfs_direction_id.count()

gtfs_direction_id
0    19
1    18
Name: gtfs_direction_id, dtype: int64

In [34]:
df[ df.ROUTE_NUMBER == 'BLANK'].DEPOT_CODE.unique()

array(['CCL'], dtype=object)